In [1]:
%cd data
lines = open("LJSpeech-1.1/metadata.csv", "r", encoding="utf-8").readlines()
for line in lines:
  i, _, transcript = line.strip().split('|')
  open(f"LJSpeech-1.1/wavs/{i}.txt", "w").write(transcript)

d:\UROP-MAIL\light-speed\data


In [2]:
!conda deactivate && conda activate aligner && \
mfa train \
    --num_jobs 5 \
    --use_mp \
    --clean \
    --overwrite \
    --no_textgrid_cleanup \
    --single_speaker \
    --output_format json \
    --output_directory LJSpeech-1.1/wavs \
    LJSpeech-1.1/wavs ./lexicon.txt ljs_mfa

Please be aware that you are running an alpha version of MFA. If you would like to install a more stable version, please visit https://montreal-forced-aligner.readthedocs.io/en/latest/installation.html#installing-older-versions-of-mfa
 INFO     Setting up corpus information...                                     
 INFO     Loading corpus from source files...                                  
 INFO     Found 1 speaker across 13100 files, average number of utterances per 
          speaker: 13100.0                                                     
 INFO     Initializing multiprocessing jobs...                                 
 INFO     Normalizing text...                                                  
 INFO     Generating MFCCs...                                                  
 INFO     Calculating CMVN...                                                  
 INFO     Generating final features...                                         
 INFO     Creating corpus split...           


   0% ----------------------------------- 0/100  [ 0:00:00 < -:--:-- , ? it/s ]
   0% ----------------------------------- 0/100  [ 0:00:00 < -:--:-- , ? it/s ]
   1% ----------------------------------- 1/100  [ 0:00:00 < -:--:-- , ? it/s ]
  38% ------------ ------------------- 38/100  [ 0:00:00 < 0:00:01 , 339 it/s ]
  78% ------------------------ ------- 78/100  [ 0:00:00 < 0:00:01 , 379 it/s ]
 100% ------------------------------- 152/100  [ 0:00:00 < 0:00:00 , 358 it/s ]
 100% ------------------------------- 189/100  [ 0:00:00 < 0:00:00 , 364 it/s ]
 100% ------------------------------- 224/100  [ 0:00:00 < 0:00:00 , 357 it/s ]
 100% ------------------------------- 224/100  [ 0:00:00 < 0:00:00 , 357 it/s ]
 100% ------------------------------- 259/100  [ 0:00:00 < 0:00:00 , 351 it/s ]
 100% ------------------------------- 295/100  [ 0:00:00 < 0:00:00 , 348 it/s ]
 100% ------------------------------- 333/100  [ 0:00:00 < 0:00:00 , 348 it/s ]
 100% ------------------------------- 4

In [3]:
import json
from pathlib import Path
import numpy as np
import torch
import json
import librosa
import tensorflow as tf
from tqdm.auto import tqdm
import random


  59% -------------- --------- 5,937/10,000  [ 0:00:04 < 0:00:04 , 1,343 it/s ]
  61% -------------- --------- 6,078/10,000  [ 0:00:04 < 0:00:03 , 1,342 it/s ]
  62% -------------- --------- 6,218/10,000  [ 0:00:04 < 0:00:03 , 1,340 it/s ]
  64% --------------- -------- 6,351/10,000  [ 0:00:04 < 0:00:03 , 1,333 it/s ]
  65% --------------- -------- 6,479/10,000  [ 0:00:04 < 0:00:03 , 1,329 it/s ]
  66% --------------- -------- 6,609/10,000  [ 0:00:05 < 0:00:03 , 1,330 it/s ]
  67% ---------------- ------- 6,747/10,000  [ 0:00:05 < 0:00:03 , 1,333 it/s ]
  69% ---------------- ------- 6,887/10,000  [ 0:00:05 < 0:00:03 , 1,332 it/s ]
  70% ---------------- ------- 7,020/10,000  [ 0:00:05 < 0:00:03 , 1,333 it/s ]
  73% ----------------- ------ 7,307/10,000  [ 0:00:05 < 0:00:03 , 1,332 it/s ]
  74% ----------------- ------ 7,444/10,000  [ 0:00:05 < 0:00:02 , 1,335 it/s ]
  76% ------------------ ----- 7,584/10,000  [ 0:00:05 < 0:00:02 , 1,337 it/s ]
  77% ------------------ ----- 7,722/10

  43% ----------- -------------- 5,570/13,100  [ 0:00:15 < 0:00:21 , 373 it/s ]
  43% ----------- -------------- 5,611/13,100  [ 0:00:15 < 0:00:21 , 373 it/s ]
  43% ----------- -------------- 5,653/13,100  [ 0:00:15 < 0:00:20 , 373 it/s ]
  43% ----------- -------------- 5,694/13,100  [ 0:00:15 < 0:00:20 , 373 it/s ]
  44% ----------- -------------- 5,734/13,100  [ 0:00:15 < 0:00:20 , 373 it/s ]
  44% ----------- -------------- 5,776/13,100  [ 0:00:15 < 0:00:20 , 374 it/s ]
  44% ----------- -------------- 5,816/13,100  [ 0:00:15 < 0:00:20 , 374 it/s ]
  45% ----------- -------------- 5,856/13,100  [ 0:00:16 < 0:00:20 , 373 it/s ]
  45% ----------- -------------- 5,899/13,100  [ 0:00:16 < 0:00:20 , 374 it/s ]
  45% ----------- -------------- 5,942/13,100  [ 0:00:16 < 0:00:20 , 374 it/s ]
  46% ----------- -------------- 5,982/13,100  [ 0:00:16 < 0:00:20 , 374 it/s ]
  46% ----------- -------------- 6,026/13,100  [ 0:00:16 < 0:00:19 , 374 it/s ]
  46% ------------ ------------- 6,067/1

In [4]:
mel_basis = {}
hann_window = {}

def spectrogram_torch(y, n_fft, sampling_rate, hop_size, win_size, center=False):
    global hann_window
    if torch.min(y) < -1.0:
        print("min value is ", torch.min(y))
    if torch.max(y) > 1.0:
        print("max value is ", torch.max(y))

    dtype_device = str(y.dtype) + "_" + str(y.device)
    wnsize_dtype_device = str(win_size) + "_" + dtype_device
    if wnsize_dtype_device not in hann_window:
        hann_window[wnsize_dtype_device] = torch.hann_window(win_size).to(
            dtype=y.dtype, device=y.device
        )

    y = torch.nn.functional.pad(
        y.unsqueeze(1),
        (int((n_fft - hop_size) / 2), int((n_fft - hop_size) / 2)),
        mode="reflect",
    )
    y = y.squeeze(1)

    spec = torch.stft(
        y,
        n_fft,
        hop_length=hop_size,
        win_length=win_size,
        window=hann_window[wnsize_dtype_device],
        center=center,
        pad_mode="reflect",
        normalized=False,
        onesided=True,
        return_complex=True
    )
    spec = torch.view_as_real(spec)
    spec = torch.sqrt(spec.pow(2).sum(-1) + 1e-6)
    spec = spec.squeeze(0)
    return torch.swapaxes(spec, 0, 1)


def tensor_to_bytes(t):
    t = tf.constant(t)
    t = tf.io.serialize_tensor(t)
    return tf.train.Feature(bytes_list=tf.train.BytesList(value=[t.numpy()]))


def write_tfdata(data, out_file):
    with tf.io.TFRecordWriter(out_file) as file_writer:
        for wav_file, seq, _ in data:
            phone_seq = []
            for phone, duration in seq:
                phone_idx = phone_set.index(phone)
                phone_seq.append((phone_idx, duration))
            phone_seq = np.array(phone_seq, dtype=np.float32)

            # load wav
            wav, sr = librosa.load(wav_file, sr=config["data"]["sampling_rate"], dtype=np.float32)
            wav = torch.from_numpy(wav)
            # compute spec
            spec = spectrogram_torch(
                wav[None],
                n_fft=config["data"]["filter_length"],
                sampling_rate=config["data"]["sampling_rate"],
                hop_size=config["data"]["hop_length"],
                win_size=config["data"]["win_length"],
                center=False
            )

            features = {
                "phone_idx": tensor_to_bytes(phone_seq[:, 0].astype(np.int32)),
                "phone_duration": tensor_to_bytes(phone_seq[:, 1]),
                "wav": tensor_to_bytes(wav.half().numpy()),
                "spec": tensor_to_bytes(spec.half().numpy())
            }
            example = tf.train.Example(features=tf.train.Features(feature=features))
            file_writer.write(example.SerializeToString())

def write_split(split, data, num_chunks):
    data = np.array(data, dtype=object)
    chunks = list(np.array_split(data, num_chunks))
    for i, chunk in enumerate(tqdm(chunks)):
        write_tfdata(chunk, f"tfdata/{split}/part_{i:03d}.tfrecords")

In [11]:
!mkdir tfdata\train, tfdata\test

In [6]:
with open("../config.json", "rb") as f:
    config = json.load(f)
device = "cuda" if torch.cuda.is_available() else "cpu"
data_dir = Path("LJSpeech-1.1/wavs")
json_files = sorted(data_dir.glob("*.json"))
dataset = []
phone_set = []

for file_path in json_files:
    with open(file_path, "rb") as f:
        data = json.load(f)
    seq = []
    word_index = 0
    words =  data["tiers"]["words"]["entries"]
    for start, end, phone in data["tiers"]["phones"]["entries"]:
        if start > words[word_index][1] - 1e-5:
            seq.append( ("<SEP>", 0) )
            word_index += 1
        duration = end * 1000 - start * 1000 # ms
        phone_set.append(phone)
        seq.append( (phone, duration) )
    wav_file = file_path.with_suffix(".wav")
    dataset.append((wav_file, seq, data["end"]))

phone_set = ["<SEP>"] + sorted(set(phone_set))
assert len(phone_set) <= 256
with open("phone_set.json", "w", encoding="utf-8") as f:
    json.dump(phone_set, f)

assert phone_set.index("<SEP>") == 0

In [7]:
random.Random(42).shuffle(dataset)
L = len(dataset) - 256
train_data = dataset[:L]
test_data = dataset[L:]
print("Train data size:", len(train_data))
print("Test data size:", len(test_data))

Train data size: 12843
Test data size: 256


In [12]:
write_split("test", test_data, 1)

  0%|          | 0/1 [00:00<?, ?it/s]

SystemError: initialization of _internal failed without raising an exception

In [13]:
write_split("train", train_data, 100)

  0%|          | 0/100 [00:00<?, ?it/s]

SystemError: initialization of _internal failed without raising an exception